### Check GPU availability

In [1]:
!nvidia-smi

Wed Feb 13 16:07:55 2019       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 384.145                Driver Version: 384.145                   |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  GeForce GTX 108...  Off  | 00000000:02:00.0 Off |                  N/A |
| 23%   27C    P8    17W / 250W |      0MiB / 11172MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   1  GeForce GTX 108...  Off  | 00000000:03:00.0 Off |                  N/A |
| 28%   51C    P5    26W / 250W |      0MiB / 11172MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
        

### Import libraries

In [2]:
import torch
import torch.utils.data
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

import copy
import numpy as np
import time
import json
import plotly
import logging
logging.getLogger().setLevel(logging.INFO)

from pprint import pprint
from tqdm import tqdm_notebook
from idst_util import trivial
from idst_util import dstc2
from dstc2.dstc2_scripts import score

from plotly.graph_objs import Scatter, Layout, Histogram, Histogram2d
from plotly.graph_objs.layout import Margin
plotly.offline.init_notebook_mode(connected = True)

[nltk_data] Downloading package punkt to /home/is/andrei-
[nltk_data]     cc/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


### Check DSTC2 availability and retrieve data

In [3]:
trivial.print_idst()

dstc2.check()

raw_X_train, raw_Y_train, \
raw_X_dev, raw_Y_dev, \
raw_X_test, raw_Y_test, \
ontology = dstc2.retrieve_raw_datasets(train_data_augmentation = True)

INFO:root:+--------------------------------+
INFO:root:|         _ ____  ___________    |
INFO:root:|        (_) __ \/ ___/_  __/    |
INFO:root:|       / / / / /\__ \ / /       |
INFO:root:|      / / /_/ /___/ // /        |
INFO:root:|     /_/_____//____//_/         |
INFO:root:|                                |
INFO:root:+--------------------------------+
INFO:root:|Incremental Dialog State Tracker|
INFO:root:+--------------------------------+
INFO:root:+--------------------------------+
INFO:root:|     Dialog State Tracker 2     |
INFO:root:|         Data Checker           |
INFO:root:+--------------------------------+
INFO:root:Looking for dstc2 directory in .
INFO:root:dstc2 was found!
INFO:root:Looking for dstc2_traindev directory in ./dstc2
INFO:root:dstc2_traindev was found!
INFO:root:Looking for dstc2_test directory in ./dstc2
INFO:root:dstc2_test was found!
INFO:root:Looking for dstc2_scripts directory in ./dstc2
INFO:root:dstc2_scripts was found!
INFO:root:Done!
INFO:root:+-

INFO:root:Extracting raw dev features


INFO:root:Reading dstc2_test.flist
INFO:root:Asserted 1117 dialogs for dstc2_test.flist
INFO:root:Extracting raw test features


INFO:root:Done!


### Set device

In [4]:
logging.info("+--------------------------------+")
logging.info("|             Device             |")
logging.info("+--------------------------------+")

GPU_ID = 1
DEVICE = torch.device("cuda:{}".format(GPU_ID) if torch.cuda.is_available() else "cpu")
if str(DEVICE) == "cpu":
    logging.warning("Running on CPU")
else:
    logging.info("Running on GPU {}".format(GPU_ID))

INFO:root:+--------------------------------+
INFO:root:|             Device             |
INFO:root:+--------------------------------+
INFO:root:Running on GPU 1


### Create vocabularies

In [5]:
logging.info("+--------------------------------+")
logging.info("|          Vocabulary            |")
logging.info("+--------------------------------+")
logging.info("Creating token_to_index, index_to_token and token_to_count dictionaries")

token_to_index = {"<unk>": 0}
index_to_token = {0: "<unk>"}
token_to_count = {"<unk>": 1}

for raw_train_dialog in tqdm_notebook(raw_X_train):
    for raw_train_turn in raw_train_dialog["turns"]:
        tokens_scores = raw_train_turn["system"] + raw_train_turn["user"]
        for token_score in tokens_scores:
            token = token_score[0]
            if token not in token_to_index:
                token_to_index[token] = len(token_to_index)
                index_to_token[len(token_to_index)] = token
                token_to_count[token] = 1
            else:
                token_to_count[token] += 1
                
assert len(token_to_index) == len(index_to_token)
assert len(token_to_index) == len(token_to_count)

logging.info("Done!")

INFO:root:+--------------------------------+
INFO:root:|          Vocabulary            |
INFO:root:+--------------------------------+
INFO:root:Creating token_to_index, index_to_token and token_to_count dictionaries


INFO:root:Done!


### Execution configuration

In [6]:
logging.info("+--------------------------------+")
logging.info("|         Configuration          |")
logging.info("+--------------------------------+")

VOCABULARY_SIZE = len(token_to_index)

# NOTE: we add +2 because of null and dontcare cases
GOAL_FOOD_DIM = len(ontology["informable"]["food"]) + 2 
GOAL_PRICERANGE_DIM = len(ontology["informable"]["pricerange"]) + 2
GOAL_NAME_DIM = len(ontology["informable"]["name"]) + 2
GOAL_AREA_DIM = len(ontology["informable"]["area"]) + 2

METHOD_DIM = len(ontology["method"])

REQUESTED_DIM = len(ontology["requestable"])

EMBEDDING_DIM = 170
ALTERED_EMBEDDING_DIM = 300
HIDDEN_DIM = 100

NUM_EPOCHS = 50
BATCH_SIZE = 10
PATIENCE = 4

PREDICTOR_DIM = 2

GOAL_LOSS_FUNCTION = nn.CrossEntropyLoss()
METHOD_LOSS_FUNCTION = nn.CrossEntropyLoss()
REQUESTED_LOSS_FUNCTION = nn.BCELoss()
PREDICTOR_LOSS_FUNCTION = nn.CrossEntropyLoss()

logging.info("VOCABULARY_SIZE:\t\t\t{}".format(VOCABULARY_SIZE))

logging.info("GOAL_FOOD_DIM:\t\t\t{}".format(GOAL_FOOD_DIM))
logging.info("GOAL_PRICERANGE_DIM:\t\t\t{}".format(GOAL_PRICERANGE_DIM))
logging.info("GOAL_NAME_DIM:\t\t\t{}".format(GOAL_NAME_DIM))
logging.info("GOAL_AREA_DIM:\t\t\t{}".format(GOAL_AREA_DIM))

logging.info("METHOD_DIM:\t\t\t\t{}".format(METHOD_DIM))

logging.info("REQUESTED_DIM:\t\t\t{}".format(REQUESTED_DIM))

logging.info("EMBEDDING_DIM:\t\t\t{}".format(EMBEDDING_DIM))
logging.info("ALTERED_EMBEDDING_DIM:\t\t{}".format(ALTERED_EMBEDDING_DIM))
logging.info("HIDDEN_DIM:\t\t\t\t{}".format(HIDDEN_DIM))

logging.info("PREDICTOR_DIM:\t\t\t{}".format(PREDICTOR_DIM))

logging.info("NUM_EPOCHS:\t\t\t\t{}".format(NUM_EPOCHS))
logging.info("BATCH_SIZE:\t\t\t\t{}".format(BATCH_SIZE))
logging.info("PATIENCE:\t\t\t\t{}".format(PATIENCE))

logging.info("GOAL_LOSS_FUNCTION:\t\t\t{}".format(GOAL_LOSS_FUNCTION))
logging.info("METHOD_LOSS_FUNCTION:\t\t\t{}".format(METHOD_LOSS_FUNCTION))
logging.info("REQUESTED_LOSS_FUNCTION:\t\t{}".format(REQUESTED_LOSS_FUNCTION))
logging.info("PREDICTOR_LOSS_FUNCTION:\t\t{}".format(PREDICTOR_LOSS_FUNCTION))

INFO:root:+--------------------------------+
INFO:root:|         Configuration          |
INFO:root:+--------------------------------+
INFO:root:VOCABULARY_SIZE:			1129
INFO:root:GOAL_FOOD_DIM:			93
INFO:root:GOAL_PRICERANGE_DIM:			5
INFO:root:GOAL_NAME_DIM:			115
INFO:root:GOAL_AREA_DIM:			7
INFO:root:METHOD_DIM:				5
INFO:root:REQUESTED_DIM:			8
INFO:root:EMBEDDING_DIM:			170
INFO:root:ALTERED_EMBEDDING_DIM:		300
INFO:root:HIDDEN_DIM:				100
INFO:root:PREDICTOR_DIM:			2
INFO:root:NUM_EPOCHS:				50
INFO:root:BATCH_SIZE:				10
INFO:root:PATIENCE:				4
INFO:root:GOAL_LOSS_FUNCTION:			CrossEntropyLoss()
INFO:root:METHOD_LOSS_FUNCTION:			CrossEntropyLoss()
INFO:root:REQUESTED_LOSS_FUNCTION:		BCELoss()
INFO:root:PREDICTOR_LOSS_FUNCTION:		CrossEntropyLoss()


### Utilities

In [7]:
def get_index_and_score(turn, token_to_index, mode, device):
    
    indices = []
    scores = []
    
    if mode == "train": # LecTrack 4.3: Out-of-Vocabulary Words
        for system_token, system_token_score in turn["system"]:
            indices.append(token_to_index[system_token])
            scores.append(system_token_score)
        for user_token, user_token_score in turn["user"]:
            if np.random.binomial(n = 1, p = 0.1) == 1:
                indices.append(token_to_index["<unk>"])
            else:
                indices.append(token_to_index[user_token])
            scores.append(user_token_score)
    else:
        tokens_scores = turn["system"] + turn["user"]
        for token, score in tokens_scores:
            if token not in token_to_index:
                indices.append(token_to_index["<unk>"])
            else:
                indices.append(token_to_index[token])
            scores.append(score)
            
    assert len(indices) == len(scores)
    
    return torch.tensor(indices, dtype = torch.long, device = device), torch.tensor(scores, dtype = torch.float, device = device)

# --------------------

class EarlyStopping():
    
    def __init__(self, min_delta = 0, patience = 0):
        
        self.min_delta = min_delta
        self.patience = patience
        self.wait = 0
        self.stopped_epoch = 0
        self.best = -np.Inf
        self.stop_training = False
    
    def on_epoch_end(self, epoch, current_value):
        if np.greater((current_value - self.min_delta), self.best):
            self.best = current_value
            self.wait = 0
        else:
            self.wait += 1
            if self.wait > self.patience:
                self.stopped_epoch = epoch
                self.stop_training = True
        return self.stop_training

# --------------------
    
def get_incremental_index_and_percentage(percentage, length):
    
    incremental_index = int(np.around(percentage * length)) - 1
    new_percentage = np.around(((incremental_index + 1) / length), decimals = 2)
    
    return incremental_index, new_percentage

# --------------------

def make_tracker(model_GoalPricerange, model_GoalArea, model_GoalName, model_GoalFood, model_Requested, model_Method, raw_X, raw_Y, dataset, percentage = 1.0):
    
    model_GoalPricerange = model_GoalPricerange.eval()
    model_GoalArea = model_GoalArea.eval()
    model_GoalName = model_GoalName.eval()
    model_GoalFood = model_GoalFood.eval()
    model_Requested = model_Requested.eval()
    model_Method = model_Method.eval()
    
    percentage_points = []
    
    with torch.no_grad():
        tracker_json = {}
        tracker_json["dataset"] = dataset
        tracker_json["sessions"] = []

        start_time = time.time()
        
        for raw_X_dialog, raw_Y_dialog in tqdm_notebook(zip(raw_X, raw_Y), total = len(raw_X)):
            
            model_GoalPricerange.hidden = model_GoalPricerange.init_hidden()
            model_GoalArea.hidden = model_GoalArea.init_hidden()
            model_GoalName.hidden = model_GoalName.init_hidden()
            model_GoalFood.hidden = model_GoalFood.init_hidden()
            model_Requested.hidden = model_Requested.init_hidden()
            model_Method.hidden = model_Method.init_hidden()
            
            session = {}
            session["session-id"] = raw_X_dialog["session-id"]
            session["turns"] = []

            for turn_num, (raw_X_turn, raw_Y_turn) in enumerate(zip(raw_X_dialog["turns"], raw_Y_dialog["turns"])):

                indices, scores = get_index_and_score(raw_X_turn, token_to_index, mode = "eval", device = DEVICE)
                
                incremental_index, new_percentage_point = get_incremental_index_and_percentage(percentage = percentage, length = len(indices))
                percentage_points.append(new_percentage_point)
                
                goal_foods, _ = model_GoalFood(indices, scores)
                goal_food = goal_foods[incremental_index]
                
                goal_priceranges, _ = model_GoalPricerange(indices, scores)
                goal_pricerange = goal_priceranges[incremental_index]
                
                goal_names, _ = model_GoalName(indices, scores)
                goal_name = goal_names[incremental_index]
                
                goal_areas, _ = model_GoalArea(indices, scores)
                goal_area = goal_areas[incremental_index]
                
                requesteds, _ = model_Requested(indices, scores, is_requested = True)
                requested = requesteds[incremental_index]
                
                methods, _ = model_Method(indices, scores)
                method = methods[incremental_index]
                
                turn = {}
                turn["num"] = turn_num
                turn["goal-labels"] = {}
                turn["goal-labels"]["food"] = retrieve_output_GoalFood(goal_food, ontology)
                turn["goal-labels"]["pricerange"] = retrieve_output_GoalPricerange(goal_pricerange, ontology)
                turn["goal-labels"]["name"] = retrieve_output_GoalName(goal_name, ontology)
                turn["goal-labels"]["area"] = retrieve_output_GoalArea(goal_area, ontology)
                turn["requested-slots"] = retrieve_output_Requested(requested, ontology)
                turn["method-label"] = retrieve_output_Method(method, ontology)
                
                session["turns"].append(turn)
                
            tracker_json["sessions"].append(session)
            
        end_time = time.time()
        tracker_json["wall-time"] = end_time - start_time
        
        return tracker_json, np.around(np.mean(np.array(percentage_points)), decimals = 2)

# --------------------
    
def get_scores(tracker, dataset, ontology):
    
    scores_dict = None

    if dataset == "dstc2_train":
        scores_dict = score.compute_score(dataset = "dstc2_train", dataroot = "dstc2/dstc2_traindev/data", tracker_output = tracker, ontology = ontology)
    elif dataset == "dstc2_dev":
        scores_dict = score.compute_score(dataset = "dstc2_dev", dataroot = "dstc2/dstc2_traindev/data", tracker_output = tracker, ontology = ontology)
    else: # dataset == "dstc2_test"
        scores_dict = score.compute_score(dataset = "dstc2_test", dataroot = "dstc2/dstc2_test/data", tracker_output = tracker, ontology = ontology)
            
    return scores_dict

# --------------------

def retrieve_gold_GoalPricerange(raw_Y, ontology, device):
    ontology_informable_pricerange = ontology["informable"]["pricerange"]
    raw_goal_pricerange = raw_Y["goal"]["pricerange"]
    goal_pricerange = 0
    if raw_goal_pricerange != None:
        if raw_goal_pricerange == "dontcare":
            goal_pricerange = 1
        else:    
            goal_pricerange = ontology_informable_pricerange.index(raw_goal_pricerange) + 2
    return torch.tensor([goal_pricerange], dtype = torch.long, device = device)

def retrieve_output_GoalPricerange(output_tensor, ontology):
    ontology_informable_pricerange = ontology["informable"]["pricerange"]
    output_tensor = output_tensor.view(-1)
    output_tensor = torch.exp(output_tensor)
    goal_pricerange_dict = {}
    goal_pricerange_dict["dontcare"] = output_tensor[1].item()
    for index in range(len(output_tensor) - 2):     
        goal_pricerange_dict[ontology_informable_pricerange[index]] = output_tensor[index + 2].item()
    return goal_pricerange_dict

# --------------------

def retrieve_gold_GoalArea(raw_Y, ontology, device):
    ontology_informable_area = ontology["informable"]["area"]
    raw_goal_area = raw_Y["goal"]["area"]
    goal_area = 0
    if raw_goal_area != None:
        if raw_goal_area == "dontcare":
            goal_area = 1
        else:    
            goal_area = ontology_informable_area.index(raw_goal_area) + 2
    return torch.tensor([goal_area], dtype = torch.long, device = device)

def retrieve_output_GoalArea(output_tensor, ontology):
    ontology_informable_area = ontology["informable"]["area"]
    output_tensor = output_tensor.view(-1)
    output_tensor = torch.exp(output_tensor)
    goal_area_dict = {}
    goal_area_dict["dontcare"] = output_tensor[1].item()
    for index in range(len(output_tensor) - 2):
        goal_area_dict[ontology_informable_area[index]] = output_tensor[index + 2].item()
    return goal_area_dict

# --------------------

def retrieve_gold_GoalName(raw_Y, ontology, device):
    ontology_informable_name = ontology["informable"]["name"]
    raw_goal_name = raw_Y["goal"]["name"]
    goal_name = 0
    if raw_goal_name != None:
        if raw_goal_name == "dontcare":
            goal_name = 1
        else:    
            goal_name = ontology_informable_name.index(raw_goal_name) + 2
    return torch.tensor([goal_name], dtype = torch.long, device = device)

def retrieve_output_GoalName(output_tensor, ontology):
    ontology_informable_name = ontology["informable"]["name"]
    output_tensor = output_tensor.view(-1)
    output_tensor = torch.exp(output_tensor)
    goal_name_dict = {}
    goal_name_dict["dontcare"] = output_tensor[1].item()
    for index in range(len(output_tensor) - 2):
        goal_name_dict[ontology_informable_name[index]] = output_tensor[index + 2].item()
    return goal_name_dict

# --------------------

def retrieve_gold_GoalFood(raw_Y, ontology, device):
    ontology_informable_food = ontology["informable"]["food"]
    raw_goal_food = raw_Y["goal"]["food"]
    goal_food = 0
    if raw_goal_food != None:
        if raw_goal_food == "dontcare":
            goal_food = 1
        else:    
            goal_food = ontology_informable_food.index(raw_goal_food) + 2
    return torch.tensor([goal_food], dtype = torch.long, device = device)

def retrieve_output_GoalFood(output_tensor, ontology):
    ontology_informable_food = ontology["informable"]["food"]
    output_tensor = output_tensor.view(-1)
    output_tensor = torch.exp(output_tensor)
    goal_food_dict = {}
    goal_food_dict["dontcare"] = output_tensor[1].item() 
    for index in range(len(output_tensor) - 2):
        goal_food_dict[ontology_informable_food[index]] = output_tensor[index + 2].item()
    return goal_food_dict

# --------------------

def retrieve_gold_Requested(raw_Y, ontology, device):
    ontology_requestable = ontology["requestable"]
    raw_gold_requested = raw_Y["requested"]
    gold_requested = np.zeros(len(ontology_requestable), dtype = float)
    if len(raw_gold_requested) != 0:
        for requested in raw_gold_requested:
            gold_requested[ontology_requestable.index(requested)] = 1.0
    return torch.tensor([gold_requested], dtype = torch.float, device = device)

def retrieve_output_Requested(output_tensor, ontology):
    ontology_requestable = ontology["requestable"]
    output_tensor = output_tensor.view(-1)
    requested_dict = {}
    for index in range(len(output_tensor)):
        probability_value = output_tensor[index].item()
        requested_dict[ontology_requestable[index]] = probability_value
    return requested_dict

# --------------------

def retrieve_gold_Method(raw_Y, ontology, device):
    ontology_method = ontology["method"]
    raw_gold_method = raw_Y["method"]
    gold_method = ontology_method.index(raw_gold_method)
    return torch.tensor([gold_method], dtype = torch.long, device = device)

def retrieve_output_Method(output_tensor, ontology):
    ontology_method = ontology["method"]
    output_tensor = output_tensor.view(-1)
    output_tensor = torch.exp(output_tensor)
    method_dict = {}
    for index in range(len(output_tensor)):
        method_dict[ontology_method[index]] = output_tensor[index].item()
    return method_dict

### iDST Model

In [8]:
class iDSTModel(nn.Module):
    
    def __init__(self, vocabulary_size, embedding_dim, altered_embedding_dim, hidden_dim, output_dim, device):
        super(iDSTModel, self).__init__()
        self.hidden_dim = hidden_dim
        self.device = device
        self.output_dim = output_dim
        self.embeddings = nn.Embedding(num_embeddings = vocabulary_size, embedding_dim = embedding_dim)
        self.altered_embeddings = nn.Linear(in_features = (embedding_dim + 1), out_features = altered_embedding_dim) # +1 for the ASR-score
        self.lstm = nn.LSTM(input_size = altered_embedding_dim, hidden_size = hidden_dim)
        self.classifier = nn.Linear(in_features = hidden_dim, out_features = output_dim)
        self.hidden = self.init_hidden()

    def init_hidden(self):
        return (torch.zeros(1, 1, self.hidden_dim, device = self.device),
                torch.zeros(1, 1, self.hidden_dim, device = self.device))

    def forward(self, indices, scores, is_requested = False):
        embeddings = self.embeddings(indices)
        embeddings_concat_score = torch.cat((embeddings, scores.unsqueeze(dim = 1)), dim = 1) 
        altered_embeddings = F.relu(self.altered_embeddings(embeddings_concat_score))
        lstm_out, self.hidden = self.lstm(altered_embeddings.view(len(indices), 1, -1), self.hidden)
        if is_requested:
            output = torch.sigmoid(self.classifier(lstm_out).view(-1, self.output_dim)), lstm_out
        else:
            output = F.log_softmax(self.classifier(lstm_out).view(-1, self.output_dim), dim = 1), lstm_out
        return output

### Goal Pricerange Model

In [9]:
model_GoalPricerange = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                                 embedding_dim = EMBEDDING_DIM,
                                 altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                                 hidden_dim = HIDDEN_DIM,
                                 output_dim = GOAL_PRICERANGE_DIM,
                                 device = DEVICE).to(DEVICE)
optimizer_GoalPricerange = optim.Adam(model_GoalPricerange.parameters(), lr = 1e-3, amsgrad = True) 

### Goal Area Model

In [10]:
model_GoalArea = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                           embedding_dim = EMBEDDING_DIM,
                           altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                           hidden_dim = HIDDEN_DIM,
                           output_dim = GOAL_AREA_DIM,
                           device = DEVICE).to(DEVICE)
optimizer_GoalArea = optim.Adam(model_GoalArea.parameters(), lr = 1e-3, amsgrad = True) 

### Goal Name Model

In [11]:
model_GoalName = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                           embedding_dim = EMBEDDING_DIM,
                           altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                           hidden_dim = HIDDEN_DIM,
                           output_dim = GOAL_NAME_DIM,
                           device = DEVICE).to(DEVICE)
optimizer_GoalName = optim.Adam(model_GoalName.parameters(), lr = 1e-3, amsgrad = True) 

### Goal Food Model

In [12]:
model_GoalFood = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                           embedding_dim = EMBEDDING_DIM,
                           altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                           hidden_dim = HIDDEN_DIM,
                           output_dim = GOAL_FOOD_DIM,
                           device = DEVICE).to(DEVICE)
optimizer_GoalFood = optim.Adam(model_GoalFood.parameters(), lr = 1e-3, amsgrad = True) 

### Requested Model

In [13]:
model_Requested = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                            embedding_dim = EMBEDDING_DIM,
                            altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                            hidden_dim = HIDDEN_DIM,
                            output_dim = REQUESTED_DIM,
                            device = DEVICE).to(DEVICE)
optimizer_Requested = optim.Adam(model_Requested.parameters(), lr = 1e-3, amsgrad = True) 

### Method Model

In [14]:
model_Method = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                         embedding_dim = EMBEDDING_DIM,
                         altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                         hidden_dim = HIDDEN_DIM,
                         output_dim = METHOD_DIM,
                         device = DEVICE).to(DEVICE)
optimizer_Method = optim.Adam(model_Method.parameters(), lr = 1e-3, amsgrad = True)

### Train iDST

In [ ]:
goal_pricerange_early_stopping = EarlyStopping(patience = PATIENCE)
goal_area_early_stopping = EarlyStopping(patience = PATIENCE)
goal_name_early_stopping = EarlyStopping(patience = PATIENCE)
goal_food_early_stopping = EarlyStopping(patience = PATIENCE)
requested_early_stopping = EarlyStopping(patience = PATIENCE)
method_early_stopping = EarlyStopping(patience = PATIENCE)

train_indices_loader = torch.utils.data.DataLoader(np.arange(raw_X_train.shape[0]), batch_size = BATCH_SIZE, shuffle = True)

for epoch in range(NUM_EPOCHS):
    
    logging.info("Epoch\t{}/{}".format(epoch + 1, NUM_EPOCHS))
    
    if not goal_pricerange_early_stopping.stop_training:
        model_GoalPricerange = model_GoalPricerange.train()
    if not goal_area_early_stopping.stop_training:
        model_GoalArea = model_GoalArea.train()
    if not goal_name_early_stopping.stop_training:
        model_GoalName = model_GoalName.train()
    if not goal_food_early_stopping.stop_training:
        model_GoalFood = model_GoalFood.train()
    if not requested_early_stopping.stop_training:
        model_Requested = model_Requested.train()
    if not method_early_stopping.stop_training:
        model_Method = model_Method.train()
    
    for train_indices in tqdm_notebook(train_indices_loader, total = len(train_indices_loader)):
        
        if not goal_pricerange_early_stopping.stop_training:
            optimizer_GoalPricerange.zero_grad()
            goal_pricerange_accumulated_loss = 0
        if not goal_area_early_stopping.stop_training:
            optimizer_GoalArea.zero_grad()
            goal_area_accumulated_loss = 0
        if not goal_name_early_stopping.stop_training:
            optimizer_GoalName.zero_grad()
            goal_name_accumulated_loss = 0
        if not goal_food_early_stopping.stop_training:
            optimizer_GoalFood.zero_grad()
            goal_food_accumulated_loss = 0
        if not requested_early_stopping.stop_training:
            optimizer_Requested.zero_grad()
            requested_accumulated_loss = 0
        if not method_early_stopping.stop_training:
            optimizer_Method.zero_grad()
            method_accumulated_loss = 0
        
        for raw_X_train_dialog, raw_Y_train_dialog in zip(raw_X_train[train_indices], raw_Y_train[train_indices]):
            
            if not goal_pricerange_early_stopping.stop_training:
                model_GoalPricerange.hidden = model_GoalPricerange.init_hidden()
            if not goal_area_early_stopping.stop_training:
                model_GoalArea.hidden = model_GoalArea.init_hidden()
            if not goal_name_early_stopping.stop_training:
                model_GoalName.hidden = model_GoalName.init_hidden()
            if not goal_food_early_stopping.stop_training:
                model_GoalFood.hidden = model_GoalFood.init_hidden()
            if not requested_early_stopping.stop_training:
                model_Requested.hidden = model_Requested.init_hidden()
            if not method_early_stopping.stop_training:
                model_Method.hidden = model_Method.init_hidden()
                
            for raw_X_train_turn, raw_Y_train_turn in zip(raw_X_train_dialog["turns"], raw_Y_train_dialog["turns"]):

                indices, scores = get_index_and_score(raw_X_train_turn, token_to_index, mode = "train", device = DEVICE)
                
                if not goal_pricerange_early_stopping.stop_training:
                    goal_pricerange_outputs, _ = model_GoalPricerange(indices, scores)
                    gold_goal_pricerange = retrieve_gold_GoalPricerange(raw_Y_train_turn, ontology = ontology, device = DEVICE).repeat(len(goal_pricerange_outputs))
                    goal_pricerange_accumulated_loss += GOAL_LOSS_FUNCTION(goal_pricerange_outputs, gold_goal_pricerange)
                if not goal_area_early_stopping.stop_training:
                    goal_area_outputs, _ = model_GoalArea(indices, scores)
                    gold_goal_area = retrieve_gold_GoalArea(raw_Y_train_turn, ontology = ontology, device = DEVICE).repeat(len(goal_area_outputs))
                    goal_area_accumulated_loss += GOAL_LOSS_FUNCTION(goal_area_outputs, gold_goal_area)
                if not goal_name_early_stopping.stop_training:
                    goal_name_outputs, _ = model_GoalName(indices, scores)
                    gold_goal_name = retrieve_gold_GoalName(raw_Y_train_turn, ontology = ontology, device = DEVICE).repeat(len(goal_name_outputs))
                    goal_name_accumulated_loss += GOAL_LOSS_FUNCTION(goal_name_outputs, gold_goal_name)
                if not goal_food_early_stopping.stop_training:
                    goal_food_outputs, _ = model_GoalFood(indices, scores)
                    gold_goal_food = retrieve_gold_GoalFood(raw_Y_train_turn, ontology = ontology, device = DEVICE).repeat(len(goal_food_outputs))
                    goal_food_accumulated_loss += GOAL_LOSS_FUNCTION(goal_food_outputs, gold_goal_food)
                if not requested_early_stopping.stop_training:
                    requested_outputs, _ = model_Requested(indices, scores, is_requested = True)
                    gold_requested = retrieve_gold_Requested(raw_Y_train_turn, ontology = ontology, device = DEVICE).repeat(requested_outputs.size(0), 1)
                    requested_accumulated_loss += REQUESTED_LOSS_FUNCTION(requested_outputs, gold_requested)
                if not method_early_stopping.stop_training:
                    method_outputs, _ = model_Method(indices, scores)
                    gold_method = retrieve_gold_Method(raw_Y_train_turn, ontology = ontology, device = DEVICE).repeat(len(method_outputs))
                    method_accumulated_loss += METHOD_LOSS_FUNCTION(method_outputs, gold_method)
        
        if not goal_pricerange_early_stopping.stop_training:
            goal_pricerange_accumulated_loss.backward()
            optimizer_GoalPricerange.step()
        if not goal_area_early_stopping.stop_training:
            goal_area_accumulated_loss.backward()
            optimizer_GoalArea.step()
        if not goal_name_early_stopping.stop_training:
            goal_name_accumulated_loss.backward()
            optimizer_GoalName.step()
        if not goal_food_early_stopping.stop_training:
            goal_food_accumulated_loss.backward()
            optimizer_GoalFood.step()
        if not requested_early_stopping.stop_training:
            requested_accumulated_loss.backward()
            optimizer_Requested.step()
        if not method_early_stopping.stop_training:
            method_accumulated_loss.backward()
            optimizer_Method.step()
        
    dev_tracker, _ = make_tracker(model_GoalPricerange, model_GoalArea, model_GoalName, model_GoalFood, model_Requested, model_Method,
                                  raw_X_dev, raw_Y_dev, dataset = "dstc2_dev", percentage = 1.0)
    
    dev_scores_dict = get_scores(dev_tracker, dataset = "dstc2_dev", ontology = ontology)
    
    logging.info(dev_scores_dict)

    goal_pricerange_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (dev_scores_dict["goal_pricerange_accuracy"]))
    goal_area_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (dev_scores_dict["goal_area_accuracy"]))
    goal_name_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (dev_scores_dict["goal_name_accuracy"]))
    goal_food_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (dev_scores_dict["goal_food_accuracy"]))
    requested_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (dev_scores_dict["requested_all_accuracy"]))
    method_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (dev_scores_dict["method_accuracy"]))
    
    if goal_pricerange_early_stopping.wait == 0:
        torch.save(model_GoalPricerange.state_dict(), "model_PANFMR_incremental_GoalPricerange.pt")
    if goal_area_early_stopping.wait == 0:
        torch.save(model_GoalArea.state_dict(), "model_PANFMR_incremental_GoalArea.pt")
    if goal_name_early_stopping.wait == 0:
        torch.save(model_GoalName.state_dict(), "model_PANFMR_incremental_GoalName.pt")
    if goal_food_early_stopping.wait == 0:
        torch.save(model_GoalFood.state_dict(), "model_PANFMR_incremental_GoalFood.pt")
    if requested_early_stopping.wait == 0:
        torch.save(model_Requested.state_dict(), "model_PANFMR_incremental_Requested.pt")
    if method_early_stopping.wait == 0:
        torch.save(model_Method.state_dict(), "model_PANFMR_incremental_Method.pt")
        
    if goal_pricerange_early_stopping.stop_training:
        model_GoalPricerange.load_state_dict(torch.load("model_PANFMR_incremental_GoalPricerange.pt"))
    if goal_area_early_stopping.stop_training:
        model_GoalArea.load_state_dict(torch.load("model_PANFMR_incremental_GoalArea.pt"))
    if goal_name_early_stopping.stop_training:
        model_GoalName.load_state_dict(torch.load("model_PANFMR_incremental_GoalName.pt"))
    if goal_food_early_stopping.stop_training:
        model_GoalFood.load_state_dict(torch.load("model_PANFMR_incremental_GoalFood.pt"))
    if requested_early_stopping.stop_training:
        model_Requested.load_state_dict(torch.load("model_PANFMR_incremental_Requested.pt"))
    if method_early_stopping.stop_training:
        model_Method.load_state_dict(torch.load("model_PANFMR_incremental_Method.pt"))
        
    if goal_pricerange_early_stopping.stop_training and goal_area_early_stopping.stop_training and goal_name_early_stopping.stop_training and \
        goal_food_early_stopping.stop_training and requested_early_stopping.stop_training and method_early_stopping.stop_training:
        break

### Load Goal Pricerange Model

In [16]:
model_GoalPricerange = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                                 embedding_dim = EMBEDDING_DIM,
                                 altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                                 hidden_dim = HIDDEN_DIM,
                                 output_dim = GOAL_PRICERANGE_DIM,
                                 device = DEVICE).to(DEVICE)
model_GoalPricerange.load_state_dict(torch.load("model_PANFMR_incremental_GoalPricerange.pt"))
model_GoalPricerange.eval()

iDSTModel(
  (embeddings): Embedding(1129, 170)
  (altered_embeddings): Linear(in_features=171, out_features=300, bias=True)
  (lstm): LSTM(300, 100)
  (classifier): Linear(in_features=100, out_features=5, bias=True)
)

### Load Goal Area Model

In [17]:
model_GoalArea = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                           embedding_dim = EMBEDDING_DIM,
                           altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                           hidden_dim = HIDDEN_DIM,
                           output_dim = GOAL_AREA_DIM,
                           device = DEVICE).to(DEVICE)
model_GoalArea.load_state_dict(torch.load("model_PANFMR_incremental_GoalArea.pt"))
model_GoalArea.eval()

iDSTModel(
  (embeddings): Embedding(1129, 170)
  (altered_embeddings): Linear(in_features=171, out_features=300, bias=True)
  (lstm): LSTM(300, 100)
  (classifier): Linear(in_features=100, out_features=7, bias=True)
)

### Load Goal Name Model

In [18]:
model_GoalName = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                           embedding_dim = EMBEDDING_DIM,
                           altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                           hidden_dim = HIDDEN_DIM,
                           output_dim = GOAL_NAME_DIM,
                           device = DEVICE).to(DEVICE)
model_GoalName.load_state_dict(torch.load("model_PANFMR_incremental_GoalName.pt"))
model_GoalName.eval()

iDSTModel(
  (embeddings): Embedding(1129, 170)
  (altered_embeddings): Linear(in_features=171, out_features=300, bias=True)
  (lstm): LSTM(300, 100)
  (classifier): Linear(in_features=100, out_features=115, bias=True)
)

### Load Goal Food Model

In [19]:
model_GoalFood = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                           embedding_dim = EMBEDDING_DIM,
                           altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                           hidden_dim = HIDDEN_DIM,
                           output_dim = GOAL_FOOD_DIM,
                           device = DEVICE).to(DEVICE)
model_GoalFood.load_state_dict(torch.load("model_PANFMR_incremental_GoalFood.pt"))
model_GoalFood.eval()

iDSTModel(
  (embeddings): Embedding(1129, 170)
  (altered_embeddings): Linear(in_features=171, out_features=300, bias=True)
  (lstm): LSTM(300, 100)
  (classifier): Linear(in_features=100, out_features=93, bias=True)
)

### Load Requested Model

In [20]:
model_Requested = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                            embedding_dim = EMBEDDING_DIM,
                            altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                            hidden_dim = HIDDEN_DIM,
                            output_dim = REQUESTED_DIM,
                            device = DEVICE).to(DEVICE)
model_Requested.load_state_dict(torch.load("model_PANFMR_incremental_Requested.pt"))
model_Requested.eval()

iDSTModel(
  (embeddings): Embedding(1129, 170)
  (altered_embeddings): Linear(in_features=171, out_features=300, bias=True)
  (lstm): LSTM(300, 100)
  (classifier): Linear(in_features=100, out_features=8, bias=True)
)

### Load Method Model

In [21]:
model_Method = iDSTModel(vocabulary_size = VOCABULARY_SIZE,
                         embedding_dim = EMBEDDING_DIM,
                         altered_embedding_dim = ALTERED_EMBEDDING_DIM,
                         hidden_dim = HIDDEN_DIM,
                         output_dim = METHOD_DIM,
                         device = DEVICE).to(DEVICE)
model_Method.load_state_dict(torch.load("model_PANFMR_incremental_Method.pt"))
model_Method.eval()

iDSTModel(
  (embeddings): Embedding(1129, 170)
  (altered_embeddings): Linear(in_features=171, out_features=300, bias=True)
  (lstm): LSTM(300, 100)
  (classifier): Linear(in_features=100, out_features=5, bias=True)
)

### Print scores

In [22]:
dev_tracker, _ = make_tracker(model_GoalPricerange,
                              model_GoalArea,
                              model_GoalName,
                              model_GoalFood,
                              model_Requested,
                              model_Method,
                              raw_X_dev, raw_Y_dev, dataset = "dstc2_dev", percentage = 1.0)
get_scores(dev_tracker, dataset = "dstc2_dev", ontology = ontology)

{'goal_food_accuracy': 0.7473369,
 'goal_food_l2': 0.37639,
 'goal_pricerange_accuracy': 0.9202234,
 'goal_pricerange_l2': 0.1298724,
 'goal_name_accuracy': 0.9065421,
 'goal_name_l2': 0.1865353,
 'goal_area_accuracy': 0.8793052,
 'goal_area_l2': 0.1960002,
 'goal_joint_accuracy': 0.6392075,
 'goal_joint_l2': 0.5219743,
 'requested_all_accuracy': 0.9621349,
 'requested_all_l2': 0.0675933,
 'method_accuracy': 0.8947232,
 'method_l2': 0.1767082}

In [23]:
test_tracker, _ = make_tracker(model_GoalPricerange,
                               model_GoalArea,
                               model_GoalName,
                               model_GoalFood,
                               model_Requested,
                               model_Method,
                               raw_X_test, raw_Y_test, dataset = "dstc2_test", percentage = 1.0)
get_scores(test_tracker, dataset = "dstc2_test", ontology = ontology)

{'goal_food_accuracy': 0.7867474,
 'goal_food_l2': 0.3400614,
 'goal_pricerange_accuracy': 0.9032499,
 'goal_pricerange_l2': 0.1570489,
 'goal_name_accuracy': 0.961326,
 'goal_name_l2': 0.0771895,
 'goal_area_accuracy': 0.8755821,
 'goal_area_l2': 0.2020645,
 'goal_joint_accuracy': 0.6488802,
 'goal_joint_l2': 0.5277477,
 'requested_all_accuracy': 0.9640563,
 'requested_all_l2': 0.056568,
 'method_accuracy': 0.9195402,
 'method_l2': 0.1317837}

### SUPERVISED TURN TAKING

### Predictor utilities

In [113]:
def get_gaps_vector(vector):
    gaps_vector = []
    
    for value in vector:
        if value == vector[-1]:
            gaps_vector.append(0)
        else:
            gaps_vector.append(1)
    
    return gaps_vector

#--------------------

def get_predictor_score(dataset, session_id, turn):
    start_time = time.time()
    
    tracker_json = {}
    tracker_json["dataset"] = dataset
    tracker_json["sessions"] = []
    
    session = {}
    session["session-id"] = session_id
    session["turns"] = [copy.deepcopy(turn)] # NOTE: copy here is needed since the scoring script is going to modify the dict
    
    tracker_json["sessions"].append(session)
        
    end_time = time.time()
    
    tracker_json["wall-time"] = end_time - start_time
    
    return get_scores(tracker_json, dataset, ontology)

#--------------------

def get_predictor_Y(model_GoalPricerange, model_GoalArea, model_GoalName, model_GoalFood, model_Requested, model_Method, dataset, ontology):
    
    predictor_Y = []
    
    if dataset == "dstc2_train":
        raw_X = raw_X_train
        raw_Y = raw_Y_train
    elif dataset == "dstc2_dev":
        raw_X = raw_X_dev
        raw_Y = raw_Y_dev
    else: # dataset == "dstc2_test"
        raw_X = raw_X_test
        raw_Y = raw_Y_test
    
    with torch.no_grad():
        
        model_GoalPricerange = model_GoalPricerange.eval()
        model_GoalArea = model_GoalArea.eval()
        model_GoalName = model_GoalName.eval()
        model_GoalFood = model_GoalFood.eval()
        model_Requested = model_Requested.eval()
        model_Method = model_Method.eval()

        for raw_X_dialog, raw_Y_dialog in tqdm_notebook(zip(raw_X, raw_Y), total = len(raw_X)):

            assert(raw_X_dialog["session-id"] == raw_Y_dialog["session-id"])

            predictor_Y_dialog = {}
            predictor_Y_dialog["session-id"] = raw_Y_dialog["session-id"]
            predictor_Y_dialog["turns"] = []

            model_GoalPricerange.hidden = model_GoalPricerange.init_hidden()
            model_GoalArea.hidden = model_GoalArea.init_hidden()
            model_GoalName.hidden = model_GoalName.init_hidden()
            model_GoalFood.hidden = model_GoalFood.init_hidden()
            model_Requested.hidden = model_Requested.init_hidden()
            model_Method.hidden = model_Method.init_hidden()
            
            for turn_num, (raw_X_turn, raw_Y_turn) in enumerate(zip(raw_X_dialog["turns"], raw_Y_dialog["turns"])):
                
                predictor_Y_turn = {}
                predictor_Y_turn["goal_pricerange_predictor"] = []
                predictor_Y_turn["goal_area_predictor"] = []
                predictor_Y_turn["goal_name_predictor"] = []
                predictor_Y_turn["goal_food_predictor"] = []
                predictor_Y_turn["requested_predictor"] = []
                predictor_Y_turn["method_predictor"] = []
            
                indices, scores = get_index_and_score(raw_X_turn, token_to_index, mode = "eval", device = DEVICE)

                goal_foods, _ = model_GoalFood(indices, scores)
                goal_priceranges, _ = model_GoalPricerange(indices, scores)
                goal_names, _ = model_GoalName(indices, scores)
                goal_areas, _ = model_GoalArea(indices, scores)
                requesteds, _ = model_Requested(indices, scores, is_requested = True)
                methods, _ = model_Method(indices, scores)

                for goal_food, goal_pricerange, goal_name, goal_area, requested, method in zip(goal_foods, goal_priceranges, goal_names, goal_areas, requesteds, methods):
                    
                    turn = {}
                    turn["num"] = turn_num
                    turn["goal-labels"] = {}
                    turn["goal-labels"]["food"] = retrieve_output_GoalFood(goal_food, ontology)
                    turn["goal-labels"]["pricerange"] = retrieve_output_GoalPricerange(goal_pricerange, ontology)
                    turn["goal-labels"]["name"] = retrieve_output_GoalName(goal_name, ontology)
                    turn["goal-labels"]["area"] = retrieve_output_GoalArea(goal_area, ontology)
                    turn["requested-slots"] = retrieve_output_Requested(requested, ontology)
                    turn["method-label"] = retrieve_output_Method(method, ontology)

                    scores_dict = get_predictor_score(dataset, raw_X_dialog["session-id"], turn)
                    
                    predictor_Y_turn["goal_pricerange_predictor"].append(scores_dict["goal_pricerange_accuracy"])
                    predictor_Y_turn["goal_area_predictor"].append(scores_dict["goal_area_accuracy"])
                    predictor_Y_turn["goal_name_predictor"].append(scores_dict["goal_name_accuracy"])
                    predictor_Y_turn["goal_food_predictor"].append(scores_dict["goal_food_accuracy"])
                    predictor_Y_turn["requested_predictor"].append(scores_dict["requested_all_accuracy"])
                    predictor_Y_turn["method_predictor"].append(scores_dict["method_accuracy"])
                
                predictor_Y_turn["goal_pricerange_predictor"] = get_gaps_vector(predictor_Y_turn["goal_pricerange_predictor"])
                predictor_Y_turn["goal_area_predictor"] = get_gaps_vector(predictor_Y_turn["goal_area_predictor"])
                predictor_Y_turn["goal_name_predictor"] = get_gaps_vector(predictor_Y_turn["goal_name_predictor"])
                predictor_Y_turn["goal_food_predictor"] = get_gaps_vector(predictor_Y_turn["goal_food_predictor"])
                predictor_Y_turn["requested_predictor"] = get_gaps_vector(predictor_Y_turn["requested_predictor"])
                predictor_Y_turn["method_predictor"] = get_gaps_vector(predictor_Y_turn["method_predictor"])
                
                predictor_Y_dialog["turns"].append(predictor_Y_turn)

            predictor_Y.append(predictor_Y_dialog)

        return np.array(predictor_Y)

#--------------------    
    
def get_predictor_loss(model_GoalPricerange, model_GoalArea, model_GoalName,
                       model_GoalFood, model_Requested, model_Method,
                       model_GoalPricerangePredictor, model_GoalAreaPredictor, model_GoalNamePredictor,
                       model_GoalFoodPredictor, model_RequestedPredictor, model_MethodPredictor,
                       raw_X, predictor_Y, device):
    
    model_GoalPricerange = model_GoalPricerange.eval()
    model_GoalArea = model_GoalArea.eval()
    model_GoalName = model_GoalName.eval()
    model_GoalFood = model_GoalFood.eval()
    model_Requested = model_Requested.eval()
    model_Method = model_Method.eval()
    
    model_GoalPricerangePredictor = model_GoalPricerangePredictor.eval()
    model_GoalAreaPredictor = model_GoalAreaPredictor.eval()
    model_GoalNamePredictor = model_GoalNamePredictor.eval()
    model_GoalFoodPredictor = model_GoalFoodPredictor.eval()
    model_RequestedPredictor = model_RequestedPredictor.eval()
    model_MethodPredictor = model_MethodPredictor.eval()
    
    losses_dict = {}
    losses_dict["goal_pricerange_loss"] = 0
    losses_dict["goal_area_loss"] = 0
    losses_dict["goal_name_loss"] = 0
    losses_dict["goal_food_loss"] = 0
    losses_dict["requested_all_loss"] = 0
    losses_dict["method_loss"] = 0
    
    with torch.no_grad():
                           
        for raw_X_dialog, predictor_Y_dialog in zip(raw_X, predictor_Y):
            
                model_GoalPricerange.hidden = model_GoalPricerange.init_hidden()
                model_GoalArea.hidden = model_GoalArea.init_hidden()
                model_GoalName.hidden = model_GoalName.init_hidden()
                model_GoalFood.hidden = model_GoalFood.init_hidden()
                model_Requested.hidden = model_Requested.init_hidden()
                model_Method.hidden = model_Method.init_hidden()

                for raw_X_turn, predictor_Y_turn in zip(raw_X_dialog["turns"], predictor_Y_dialog["turns"]):
                    
                    indices, scores = get_index_and_score(raw_X_turn, token_to_index, mode = "eval", device = DEVICE)
                    
                    _, goal_pricerange_hidden_vectors = model_GoalPricerange(indices, scores)
                    goal_pricerange_outputs = model_GoalPricerangePredictor(goal_pricerange_hidden_vectors)
                    gold_goal_pricerange = torch.tensor(predictor_Y_turn["goal_pricerange_predictor"], dtype = torch.long, device = DEVICE)
                    losses_dict["goal_pricerange_loss"] += PREDICTOR_LOSS_FUNCTION(goal_pricerange_outputs, gold_goal_pricerange)
                    
                    _, goal_area_hidden_vectors = model_GoalArea(indices, scores)
                    goal_area_outputs = model_GoalAreaPredictor(goal_area_hidden_vectors)
                    gold_goal_area = torch.tensor(predictor_Y_turn["goal_area_predictor"], dtype = torch.long, device = DEVICE)
                    losses_dict["goal_area_loss"] += PREDICTOR_LOSS_FUNCTION(goal_area_outputs, gold_goal_area)
                    
                    _, goal_name_hidden_vectors = model_GoalName(indices, scores)
                    goal_name_outputs = model_GoalNamePredictor(goal_name_hidden_vectors)
                    gold_goal_name = torch.tensor(predictor_Y_turn["goal_name_predictor"], dtype = torch.long, device = DEVICE)
                    losses_dict["goal_name_loss"] += PREDICTOR_LOSS_FUNCTION(goal_name_outputs, gold_goal_name)
                    
                    _, goal_food_hidden_vectors = model_GoalFood(indices, scores)
                    goal_food_outputs = model_GoalFoodPredictor(goal_food_hidden_vectors)
                    gold_goal_food = torch.tensor(predictor_Y_turn["goal_food_predictor"], dtype = torch.long, device = DEVICE)
                    losses_dict["goal_food_loss"] += PREDICTOR_LOSS_FUNCTION(goal_food_outputs, gold_goal_food)
                    
                    _, requested_hidden_vectors = model_Requested(indices, scores)
                    requested_outputs = model_RequestedPredictor(requested_hidden_vectors)
                    gold_requested = torch.tensor(predictor_Y_turn["requested_predictor"], dtype = torch.long, device = DEVICE)
                    losses_dict["requested_all_loss"] += PREDICTOR_LOSS_FUNCTION(requested_outputs, gold_requested)
                    
                    _, method_hidden_vectors = model_Method(indices, scores)
                    method_outputs = model_MethodPredictor(method_hidden_vectors)
                    gold_method = torch.tensor(predictor_Y_turn["method_predictor"], dtype = torch.long, device = DEVICE)
                    losses_dict["method_loss"] += PREDICTOR_LOSS_FUNCTION(method_outputs, gold_method)
    
    losses_dict["goal_pricerange_loss"] = losses_dict["goal_pricerange_loss"].item()
    losses_dict["goal_area_loss"] = losses_dict["goal_area_loss"].item()
    losses_dict["goal_name_loss"] = losses_dict["goal_name_loss"].item()
    losses_dict["goal_food_loss"] = losses_dict["goal_food_loss"].item()
    losses_dict["requested_all_loss"] = losses_dict["requested_all_loss"].item()
    losses_dict["method_loss"] = losses_dict["method_loss"].item()
    
    return losses_dict

#--------------------

def make_predictor_tracker(model_GoalPricerange, model_GoalArea, model_GoalName, model_GoalFood, model_Requested, model_Method,
                           model_GoalPricerangePredictor, model_GoalAreaPredictor, model_GoalNamePredictor, model_GoalFoodPredictor, model_RequestedPredictor, model_MethodPredictor,
                           raw_X, raw_Y, dataset, threshold = 0.5):
    
    model_GoalPricerange = model_GoalPricerange.eval()
    model_GoalArea = model_GoalArea.eval()
    model_GoalName = model_GoalName.eval()
    model_GoalFood = model_GoalFood.eval()
    model_Requested = model_Requested.eval()
    model_Method = model_Method.eval()
    
    model_GoalPricerangePredictor = model_GoalPricerangePredictor.eval()
    model_GoalAreaPredictor = model_GoalAreaPredictor.eval()
    model_GoalNamePredictor = model_GoalNamePredictor.eval()
    model_GoalFoodPredictor = model_GoalFoodPredictor.eval()
    model_RequestedPredictor = model_RequestedPredictor.eval()
    model_MethodPredictor = model_MethodPredictor.eval()
    
    percentage_points = []
    token_points = []
    
    with torch.no_grad():
        
        tracker_json = {}
        tracker_json["dataset"] = dataset
        tracker_json["sessions"] = []

        start_time = time.time()
        
        for raw_X_dialog, raw_Y_dialog in tqdm_notebook(zip(raw_X, raw_Y), total = len(raw_X)):
            
            model_GoalPricerange.hidden = model_GoalPricerange.init_hidden()
            model_GoalArea.hidden = model_GoalArea.init_hidden()
            model_GoalName.hidden = model_GoalName.init_hidden()
            model_GoalFood.hidden = model_GoalFood.init_hidden()
            model_Requested.hidden = model_Requested.init_hidden()
            model_Method.hidden = model_Method.init_hidden()
            
            session = {}
            session["session-id"] = raw_X_dialog["session-id"]
            session["turns"] = []

            for turn_num, (raw_X_turn, raw_Y_turn) in enumerate(zip(raw_X_dialog["turns"], raw_Y_dialog["turns"])):
                
                take_turn = False
                
                turn = {}

                indices, scores = get_index_and_score(raw_X_turn, token_to_index, mode = "eval", device = DEVICE)
                
                
                goal_priceranges, goal_pricerange_hidden_vectors = model_GoalPricerange(indices, scores)
                goal_priceranges_predictor = torch.exp(model_GoalPricerangePredictor(goal_pricerange_hidden_vectors))
                
                goal_names, goal_pricerange_hidden_vectors = model_GoalName(indices, scores)
                goal_names_predictor = torch.exp(model_GoalNamePredictor(goal_name_hidden_vectors))
                
                goal_areas, goal_area_hidden_vectors = model_GoalArea(indices, scores)
                goal_areas_predictor = torch.exp(model_GoalAreaPredictor(goal_area_hidden_vectors))
                
                goal_foods, goal_food_hidden_vectors = model_GoalFood(indices, scores)
                goal_foods_predictor = torch.exp(model_GoalFoodPredictor(goal_food_hidden_vectors))
                
                requesteds, requested_hidden_vectors = model_Requested(indices, scores, is_requested = True)
                requesteds_predictor = torch.exp(model_RequestedPredictor(requested_hidden_vectors))
                
                methods, method_hidden_vectors = model_Method(indices, scores)
                methods_predictor = torch.exp(model_MethodPredictor(method_hidden_vectors))
                
                sentence = raw_X_turn["system"] + raw_X_turn["user"]
                
                for index, (goal_pricerange_predictor, goal_name_predictor, goal_area_predictor, goal_food_predictor, requested_predictor, method_predictor) in\
                    enumerate(zip(goal_priceranges_predictor, goal_names_predictor, goal_areas_predictor, goal_foods_predictor, requesteds_predictor, methods_predictor)):
                    
                    if (goal_pricerange_predictor[0].item() >= threshold) and (goal_name_predictor[0].item() >= threshold) and (goal_area_predictor[0].item() >= threshold) and\
                        (goal_food_predictor[0].item() >= threshold) and (requested_predictor[0].item() >= threshold) and (method_predictor[0].item() >= threshold):
                        
                        turn["num"] = turn_num
                        turn["goal-labels"] = {}
                        turn["goal-labels"]["pricerange"] = retrieve_output_GoalPricerange(goal_priceranges[index], ontology)
                        turn["goal-labels"]["area"] = retrieve_output_GoalArea(goal_areas[index], ontology)
                        turn["goal-labels"]["name"] = retrieve_output_GoalName(goal_names[index], ontology)
                        turn["goal-labels"]["food"] = retrieve_output_GoalFood(goal_foods[index], ontology)
                        turn["requested-slots"] = retrieve_output_Requested(requesteds[index], ontology)
                        turn["method-label"] = retrieve_output_Method(methods[index], ontology)
                        
                        session["turns"].append(turn)
                        
                        percentage_point = np.around((index + 1) / (len(raw_X_turn["system"]) + len(raw_X_turn["user"])), decimals = 2)
                        percentage_points.append(percentage_point)
                        token_points.append(index + 1)
                        take_turn = True
                        break
                        
                if not turn: # in case if no prediction for the turn
                    turn["num"] = turn_num
                    turn["goal-labels"] = {}
                    turn["goal-labels"]["food"] = retrieve_output_GoalFood(goal_foods[-1], ontology)
                    turn["goal-labels"]["pricerange"] = retrieve_output_GoalPricerange(goal_priceranges[-1], ontology)
                    turn["goal-labels"]["name"] = retrieve_output_GoalName(goal_names[-1], ontology)
                    turn["goal-labels"]["area"] = retrieve_output_GoalArea(goal_areas[-1], ontology)
                    turn["requested-slots"] = retrieve_output_Requested(requesteds[-1], ontology)
                    turn["method-label"] = retrieve_output_Method(methods[-1], ontology)
                    
                    session["turns"].append(turn)
                    
                    percentage_points.append(1.0)
                    token_points.append(len(raw_X_turn["system"]) + len(raw_X_turn["user"]))
                    take_turn = True
                
            tracker_json["sessions"].append(session)
            
        end_time = time.time()
        tracker_json["wall-time"] = end_time - start_time
        
        assert(len(percentage_points) == len(token_points))
        
        return tracker_json, np.around(np.mean(np.array(percentage_points)), decimals = 2), percentage_points, token_points

#--------------------
    
def frange(start, stop, step):
    i = start
    while i < stop:
        i = np.around(i, decimals = 2)
        yield i
        i += step    
    
#--------------------

def plotly_plot_histogram(data, dataset):
    if dataset == "dstc2_train":
        dataset = "TRAIN"
    elif dataset == "dstc2_dev":
        dataset = "DEV"
    else:
        dataset = "TEST"
    plotly.offline.iplot({"data": [Histogram(x = data, histnorm = "probability", xbins = dict(size = 0.025), marker = dict(color = "#3498db"))],
                          "layout": Layout(title = "<b>{} Percentage - Accuracy</b>".format(dataset),
                                           xaxis = dict(title = "<b>Percentage</b>",
                                                        dtick = 0.025,
                                                        titlefont = dict(color = "#34495e")),
                                           yaxis = dict(title = "<b>Normalized counts</b>",
                                                        dtick = 0.025,
                                                        titlefont = dict(color = "#34495e")),
                                           margin = Margin(b = 150))})

#--------------------

def plotly_plot_histogram2d(x_axis, y_axis, dataset):
    if dataset == "dstc2_train":
        dataset = "TRAIN"
    elif dataset == "dstc2_dev":
        dataset = "DEV"
    else:
        dataset = "TEST"
    plotly.offline.iplot({"data": [Histogram2d(x = x_axis, y = y_axis, xbins = dict(size = 0.05), ybins = dict(size = 1))],
                          "layout": Layout(title = "<b>{} Percentages - Tokens </b>".format(dataset),
                                           xaxis = dict(title = "<b> Percentages </b>",
                                                        dtick = 0.05,
                                                        titlefont = dict(color = "#34495e")),
                                           yaxis = dict(title = "<b> Tokens </b>",
                                                        dtick = 1,
                                                        titlefont = dict(color = "#34495e")),
                                           height = 750,
                                           width = 750)})

#--------------------

def plotly_plot_incremental(goal_pricerange_accuracies, goal_area_accuracies, goal_name_accuracies, goal_food_accuracies,
                            requested_accuracies, method_accuracies, percentages, predictor_percentage_point, predictor_goal_pricerange_accuracy,
                            predictor_goal_area_accuracy, predictor_goal_name_accuracy, predictor_goal_food_accuracy,
                            predictor_requested_accuracy, predictor_method_accuracy, dataset):
    
    if dataset == "dstc2_train":
        dataset = "TRAIN"
    elif dataset == "dstc2_dev":
        dataset = "DEV"
    else:
        dataset = "TEST"
        
    plotly.offline.iplot({"data": [Scatter(x = percentages, y = goal_pricerange_accuracies, mode = "lines+markers", name = "{} Goal Pricerange Accuracy".format(dataset), marker = dict(color = "#1abc9c")),
                                   Scatter(x = percentages, y = goal_area_accuracies, mode = "lines+markers", name = "{} Goal Area Accuracy".format(dataset), marker = dict(color = "#3498db")),
                                   Scatter(x = percentages, y = goal_name_accuracies, mode = "lines+markers", name = "{} Goal Name Accuracy".format(dataset), marker = dict(color = "#9b59b6")),
                                   Scatter(x = percentages, y = goal_food_accuracies, mode = "lines+markers", name = "{} Goal Food Accuracy".format(dataset), marker = dict(color = "#e74c3c")),
                                   Scatter(x = percentages, y = requested_accuracies, mode = "lines+markers", name = "{} Requested Accuracy".format(dataset), marker = dict(color = "#34495e")),
                                   Scatter(x = percentages, y = method_accuracies, mode = "lines+markers", name = "{} Method Accuracy".format(dataset), marker = dict(color = "#f1c40f")),
                                   Scatter(x = [predictor_percentage_point], y = [predictor_goal_pricerange_accuracy], mode = "markers", name = "{} (iSTT) Goal Pricerange Accuracy".format(dataset), marker = dict(color = "#1abc9c")),
                                   Scatter(x = [predictor_percentage_point], y = [predictor_goal_area_accuracy], mode = "markers", name = "{} (iSTT) Goal Area Accuracy".format(dataset), marker = dict(color = "#3498db")),
                                   Scatter(x = [predictor_percentage_point], y = [predictor_goal_name_accuracy], mode = "markers", name = "{} (iSTT) Goal Name Accuracy".format(dataset), marker = dict(color = "#9b59b6")),
                                   Scatter(x = [predictor_percentage_point], y = [predictor_goal_food_accuracy], mode = "markers", name = "{} (iSTT) Goal Food Accuracy".format(dataset), marker = dict(color = "#e74c3c")),
                                   Scatter(x = [predictor_percentage_point], y = [predictor_requested_accuracy], mode = "markers", name = "{} (iSTT) Requested Accuracy".format(dataset), marker = dict(color = "#34495e")),
                                   Scatter(x = [predictor_percentage_point], y = [predictor_method_accuracy], mode = "markers", name = "{} (iSTT) Method Accuracy".format(dataset), marker = dict(color = "#f1c40f"))],      
                            "layout": Layout(title = "<b>{} Percentage - Accuracy</b>".format(dataset),
                                             xaxis = dict(title = "<b>Percentage</b>",
                                                          dtick = 0.05,
                                                          titlefont = dict(color = "#34495e")),
                                             yaxis = dict(title = "<b>Accuracy</b>",
                                                          dtick = 0.025,
                                                          titlefont = dict(color = "#34495e")),
                                             margin = Margin(b = 150))})

### Compute and save development set predictor labels

In [ ]:
dev_predictor_Y = get_predictor_Y(model_GoalPricerange,
                                  model_GoalArea,
                                  model_GoalName,
                                  model_GoalFood,
                                  model_Requested,
                                  model_Method,
                                  "dstc2_dev",
                                  ontology)
np.save("dev_predictor_Y", dev_predictor_Y)

### Load development set predictor labels

In [26]:
dev_predictor_Y = np.load("dev_predictor_Y.npy")

### Compute and save train set predictor labels

In [ ]:
train_predictor_Y = get_predictor_Y(model_GoalPricerange,
                                    model_GoalArea,
                                    model_GoalName,
                                    model_GoalFood,
                                    model_Requested,
                                    model_Method,
                                    "dstc2_train",
                                    ontology)
np.save("train_predictor_Y", train_predictor_Y)

### Load train set predictor labels

In [28]:
train_predictor_Y = np.load("train_predictor_Y.npy")

### iDST Predictor Model

In [38]:
class iDSTPredictorModel(nn.Module):
    
    def __init__(self, hidden_dim, output_dim, device):
        super(iDSTPredictorModel, self).__init__()
        self.device = device
        self.hidden_dim = hidden_dim
        self.output_dim = output_dim
        self.classifier = nn.Linear(in_features = hidden_dim, out_features = output_dim)

    def forward(self, hidden_vectors):
        output = F.log_softmax(self.classifier(hidden_vectors).view(-1, self.output_dim), dim = 1)
        return output

### Goal Pricerange Predictor Model

In [39]:
model_GoalPricerangePredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                                   output_dim = PREDICTOR_DIM,
                                                   device = DEVICE).to(DEVICE)
optimizer_GoalPricerangePredictor = optim.Adam(model_GoalPricerangePredictor.parameters(), lr = 1e-3, amsgrad = True)

### Goal Area Predictor Model

In [40]:
model_GoalAreaPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                             output_dim = PREDICTOR_DIM,
                                             device = DEVICE).to(DEVICE)
optimizer_GoalAreaPredictor = optim.Adam(model_GoalAreaPredictor.parameters(), lr = 1e-3, amsgrad = True)

### Goal Name Predictor Model

In [41]:
model_GoalNamePredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                             output_dim = PREDICTOR_DIM,
                                             device = DEVICE).to(DEVICE)
optimizer_GoalNamePredictor = optim.Adam(model_GoalNamePredictor.parameters(), lr = 1e-3, amsgrad = True)

### Goal Food Predictor Model

In [42]:
model_GoalFoodPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                             output_dim = PREDICTOR_DIM,
                                             device = DEVICE).to(DEVICE)
optimizer_GoalFoodPredictor = optim.Adam(model_GoalFoodPredictor.parameters(), lr = 1e-3, amsgrad = True)

### Requested Predictor Model

In [43]:
model_RequestedPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                             output_dim = PREDICTOR_DIM,
                                             device = DEVICE).to(DEVICE)
optimizer_RequestedPredictor = optim.Adam(model_RequestedPredictor.parameters(), lr = 1e-3, amsgrad = True)

### Method Predictor Model

In [44]:
model_MethodPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                           output_dim = PREDICTOR_DIM,
                                           device = DEVICE).to(DEVICE)
optimizer_MethodPredictor = optim.Adam(model_MethodPredictor.parameters(), lr = 1e-3, amsgrad = True)

### Train iDST Predictor

In [45]:
goal_pricerange_predictor_early_stopping = EarlyStopping(patience = PATIENCE)
goal_area_predictor_early_stopping = EarlyStopping(patience = PATIENCE)
goal_name_predictor_early_stopping = EarlyStopping(patience = PATIENCE)
goal_food_predictor_early_stopping = EarlyStopping(patience = PATIENCE)
requested_predictor_early_stopping = EarlyStopping(patience = PATIENCE)
method_predictor_early_stopping = EarlyStopping(patience = PATIENCE)

train_indices_loader = torch.utils.data.DataLoader(np.arange(raw_X_train.shape[0]), batch_size = BATCH_SIZE, shuffle = True)

for epoch in range(NUM_EPOCHS):
    
    logging.info("Epoch\t{}/{}".format(epoch + 1, NUM_EPOCHS))
    
    if not goal_pricerange_predictor_early_stopping.stop_training:
        model_GoalPricerange = model_GoalPricerange.eval()
        model_GoalPricerangePredictor = model_GoalPricerangePredictor.train()
    if not goal_area_predictor_early_stopping.stop_training:
        model_GoalArea = model_GoalArea.eval()
        model_GoalAreaPredictor = model_GoalAreaPredictor.train()
    if not goal_name_predictor_early_stopping.stop_training:
        model_GoalName = model_GoalName.eval()
        model_GoalNamePredictor = model_GoalNamePredictor.train()
    if not goal_food_predictor_early_stopping.stop_training:
        model_GoalFood = model_GoalFood.eval()
        model_GoalFoodPredictor = model_GoalFoodPredictor.train()
    if not requested_predictor_early_stopping.stop_training:
        model_Requested = model_Requested.eval()
        model_RequestedPredictor = model_RequestedPredictor.train()
    if not method_predictor_early_stopping.stop_training:
        model_Method = model_Method.eval()
        model_MethodPredictor = model_MethodPredictor.train()
    
    for train_indices in tqdm_notebook(train_indices_loader, total = len(train_indices_loader)):
        
        if not goal_pricerange_predictor_early_stopping.stop_training:
            optimizer_GoalPricerangePredictor.zero_grad()
            goal_pricerange_accumulated_loss = 0
        if not goal_area_predictor_early_stopping.stop_training:
            optimizer_GoalAreaPredictor.zero_grad()
            goal_area_accumulated_loss = 0
        if not goal_name_predictor_early_stopping.stop_training:
            optimizer_GoalNamePredictor.zero_grad()
            goal_name_accumulated_loss = 0
        if not goal_food_predictor_early_stopping.stop_training:
            optimizer_GoalFoodPredictor.zero_grad()
            goal_food_accumulated_loss = 0
        if not requested_predictor_early_stopping.stop_training:
            optimizer_RequestedPredictor.zero_grad()
            requested_accumulated_loss = 0
        if not method_predictor_early_stopping.stop_training:
            optimizer_MethodPredictor.zero_grad()
            method_accumulated_loss = 0
        
        for raw_X_train_dialog, train_predictor_Y_dialog in zip(raw_X_train[train_indices], train_predictor_Y[train_indices]):
            
            if not goal_pricerange_predictor_early_stopping.stop_training:
                model_GoalPricerange.hidden = model_GoalPricerange.init_hidden()
            if not goal_area_predictor_early_stopping.stop_training:
                model_GoalArea.hidden = model_GoalArea.init_hidden()
            if not goal_name_predictor_early_stopping.stop_training:
                model_GoalName.hidden = model_GoalName.init_hidden()
            if not goal_food_predictor_early_stopping.stop_training:
                model_GoalFood.hidden = model_GoalFood.init_hidden()
            if not requested_predictor_early_stopping.stop_training:
                model_Requested.hidden = model_Requested.init_hidden()
            if not method_predictor_early_stopping.stop_training:
                model_Method.hidden = model_Method.init_hidden()
                
            for raw_X_train_turn, train_predictor_Y_turn in zip(raw_X_train_dialog["turns"], train_predictor_Y_dialog["turns"]):

                indices, scores = get_index_and_score(raw_X_train_turn, token_to_index, mode = "train", device = DEVICE)
                
                if not goal_pricerange_predictor_early_stopping.stop_training:
                    with torch.no_grad():
                        _, goal_pricerange_hidden_vectors = model_GoalPricerange(indices, scores)
                    goal_pricerange_outputs = model_GoalPricerangePredictor(goal_pricerange_hidden_vectors)
                    gold_goal_pricerange = torch.tensor(train_predictor_Y_turn["goal_pricerange_predictor"], dtype = torch.long, device = DEVICE)
                    goal_pricerange_accumulated_loss += PREDICTOR_LOSS_FUNCTION(goal_pricerange_outputs, gold_goal_pricerange)
                if not goal_area_predictor_early_stopping.stop_training:
                    with torch.no_grad():
                        _, goal_area_hidden_vectors = model_GoalArea(indices, scores)
                    goal_area_outputs = model_GoalAreaPredictor(goal_area_hidden_vectors)
                    gold_goal_area = torch.tensor(train_predictor_Y_turn["goal_area_predictor"], dtype = torch.long, device = DEVICE)
                    goal_area_accumulated_loss += PREDICTOR_LOSS_FUNCTION(goal_area_outputs, gold_goal_area)
                if not goal_name_predictor_early_stopping.stop_training:
                    with torch.no_grad():
                        _, goal_name_hidden_vectors = model_GoalName(indices, scores)
                    goal_name_outputs = model_GoalNamePredictor(goal_name_hidden_vectors)
                    gold_goal_name = torch.tensor(train_predictor_Y_turn["goal_name_predictor"], dtype = torch.long, device = DEVICE)
                    goal_name_accumulated_loss += PREDICTOR_LOSS_FUNCTION(goal_name_outputs, gold_goal_name)
                if not goal_food_predictor_early_stopping.stop_training:
                    with torch.no_grad():
                        _, goal_food_hidden_vectors = model_GoalFood(indices, scores)
                    goal_food_outputs = model_GoalFoodPredictor(goal_food_hidden_vectors)
                    gold_goal_food = torch.tensor(train_predictor_Y_turn["goal_food_predictor"], dtype = torch.long, device = DEVICE)
                    goal_food_accumulated_loss += PREDICTOR_LOSS_FUNCTION(goal_food_outputs, gold_goal_food)
                if not requested_predictor_early_stopping.stop_training:
                    with torch.no_grad():
                        _, requested_hidden_vectors = model_Requested(indices, scores, is_requested = True)
                    requested_outputs = model_RequestedPredictor(requested_hidden_vectors)
                    gold_requested = torch.tensor(train_predictor_Y_turn["requested_predictor"], dtype = torch.long, device = DEVICE)
                    requested_accumulated_loss += PREDICTOR_LOSS_FUNCTION(requested_outputs, gold_requested)
                if not method_predictor_early_stopping.stop_training:
                    with torch.no_grad():
                        _, method_hidden_vectors = model_Method(indices, scores)
                    method_outputs = model_MethodPredictor(method_hidden_vectors)
                    gold_method = torch.tensor(train_predictor_Y_turn["method_predictor"], dtype = torch.long, device = DEVICE)
                    method_accumulated_loss += PREDICTOR_LOSS_FUNCTION(method_outputs, gold_method)
        
        if not goal_pricerange_predictor_early_stopping.stop_training:
            goal_pricerange_accumulated_loss.backward()
            optimizer_GoalPricerangePredictor.step()
        if not goal_area_predictor_early_stopping.stop_training:
            goal_area_accumulated_loss.backward()
            optimizer_GoalAreaPredictor.step()
        if not goal_name_predictor_early_stopping.stop_training:
            goal_name_accumulated_loss.backward()
            optimizer_GoalNamePredictor.step()
        if not goal_food_predictor_early_stopping.stop_training:
            goal_food_accumulated_loss.backward()
            optimizer_GoalFoodPredictor.step()
        if not requested_predictor_early_stopping.stop_training:
            requested_accumulated_loss.backward()
            optimizer_RequestedPredictor.step()
        if not method_predictor_early_stopping.stop_training:
            method_accumulated_loss.backward()
            optimizer_MethodPredictor.step()

    dev_losses_dict = get_predictor_loss(model_GoalPricerange, model_GoalArea, model_GoalName,
                                         model_GoalFood, model_Requested, model_Method,
                                         model_GoalPricerangePredictor, model_GoalAreaPredictor, model_GoalNamePredictor,
                                         model_GoalFoodPredictor, model_RequestedPredictor, model_MethodPredictor,
                                         raw_X_dev, dev_predictor_Y, DEVICE)
    
    logging.info(dev_losses_dict)

    goal_pricerange_predictor_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (-dev_losses_dict["goal_pricerange_loss"]))
    goal_area_predictor_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (-dev_losses_dict["goal_area_loss"]))
    goal_name_predictor_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (-dev_losses_dict["goal_name_loss"]))
    goal_food_predictor_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (-dev_losses_dict["goal_food_loss"]))
    requested_predictor_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (-dev_losses_dict["requested_all_loss"]))
    method_predictor_early_stopping.on_epoch_end(epoch = (epoch + 1), current_value = (-dev_losses_dict["method_loss"]))
    
    if goal_pricerange_predictor_early_stopping.wait == 0:
        torch.save(model_GoalPricerangePredictor.state_dict(), "model_PANFMR_incremental_GoalPricerangePredictor.pt")
    if goal_area_predictor_early_stopping.wait == 0:
        torch.save(model_GoalAreaPredictor.state_dict(), "model_PANFMR_incremental_GoalAreaPredictor.pt")
    if goal_name_predictor_early_stopping.wait == 0:
        torch.save(model_GoalNamePredictor.state_dict(), "model_PANFMR_incremental_GoalNamePredictor.pt")
    if goal_food_predictor_early_stopping.wait == 0:
        torch.save(model_GoalFoodPredictor.state_dict(), "model_PANFMR_incremental_GoalFoodPredictor.pt")
    if requested_predictor_early_stopping.wait == 0:
        torch.save(model_RequestedPredictor.state_dict(), "model_PANFMR_incremental_RequestedPredictor.pt")
    if method_predictor_early_stopping.wait == 0:
        torch.save(model_MethodPredictor.state_dict(), "model_PANFMR_incremental_MethodPredictor.pt")
        
    if goal_pricerange_predictor_early_stopping.stop_training:
        model_GoalPricerangePredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalPricerangePredictor.pt"))
    if goal_area_predictor_early_stopping.stop_training:
        model_GoalAreaPredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalAreaPredictor.pt"))
    if goal_name_predictor_early_stopping.stop_training:
        model_GoalNamePredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalNamePredictor.pt"))
    if goal_food_predictor_early_stopping.stop_training:
        model_GoalFoodPredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalFoodPredictor.pt"))
    if requested_predictor_early_stopping.stop_training:
        model_RequestedPredictor.load_state_dict(torch.load("model_PANFMR_incremental_RequestedPredictor.pt"))
    if method_predictor_early_stopping.stop_training:
        model_MethodPredictor.load_state_dict(torch.load("model_PANFMR_incremental_MethodPredictor.pt"))
        
    if goal_pricerange_predictor_early_stopping.stop_training and goal_area_predictor_early_stopping.stop_training and \
        goal_name_predictor_early_stopping.stop_training and goal_food_predictor_early_stopping.stop_training and \
        requested_predictor_early_stopping.stop_training and method_predictor_early_stopping.stop_training:
        break

INFO:root:Epoch	1/50


INFO:root:{'goal_pricerange_loss': 538.3095703125, 'goal_area_loss': 591.1871948242188, 'goal_name_loss': 7.268874645233154, 'goal_food_loss': 878.3562622070312, 'requested_all_loss': 1164.42236328125, 'method_loss': 969.1655883789062}
INFO:root:Epoch	2/50


INFO:root:{'goal_pricerange_loss': 479.97125244140625, 'goal_area_loss': 572.1472778320312, 'goal_name_loss': 2.9442391395568848, 'goal_food_loss': 840.7046508789062, 'requested_all_loss': 1148.0185546875, 'method_loss': 942.078369140625}
INFO:root:Epoch	3/50


INFO:root:{'goal_pricerange_loss': 460.4880065917969, 'goal_area_loss': 566.0116577148438, 'goal_name_loss': 1.7331000566482544, 'goal_food_loss': 837.6368408203125, 'requested_all_loss': 1146.1434326171875, 'method_loss': 930.7142944335938}
INFO:root:Epoch	4/50


INFO:root:{'goal_pricerange_loss': 451.0030517578125, 'goal_area_loss': 559.3410034179688, 'goal_name_loss': 1.1948422193527222, 'goal_food_loss': 826.56103515625, 'requested_all_loss': 1140.2025146484375, 'method_loss': 919.8805541992188}
INFO:root:Epoch	5/50


...

INFO:root:{'goal_pricerange_loss': 421.2474670410156, 'goal_area_loss': 545.0855712890625, 'goal_name_loss': 0.07575607299804688, 'goal_food_loss': 820.1277465820312, 'requested_all_loss': 1111.31689453125, 'method_loss': 904.2598876953125}
INFO:root:Epoch	47/50


INFO:root:{'goal_pricerange_loss': 421.3717041015625, 'goal_area_loss': 545.0855712890625, 'goal_name_loss': 0.07411769777536392, 'goal_food_loss': 820.1277465820312, 'requested_all_loss': 1111.31689453125, 'method_loss': 904.2598876953125}
INFO:root:Epoch	48/50


INFO:root:{'goal_pricerange_loss': 422.2388610839844, 'goal_area_loss': 545.0855712890625, 'goal_name_loss': 0.07255684584379196, 'goal_food_loss': 820.1277465820312, 'requested_all_loss': 1111.31689453125, 'method_loss': 904.2598876953125}
INFO:root:Epoch	49/50


INFO:root:{'goal_pricerange_loss': 421.03070068359375, 'goal_area_loss': 545.0855712890625, 'goal_name_loss': 0.07108717411756516, 'goal_food_loss': 820.1277465820312, 'requested_all_loss': 1111.31689453125, 'method_loss': 904.2598876953125}
INFO:root:Epoch	50/50


INFO:root:{'goal_pricerange_loss': 421.3023376464844, 'goal_area_loss': 545.0855712890625, 'goal_name_loss': 0.06962546706199646, 'goal_food_loss': 820.1277465820312, 'requested_all_loss': 1111.31689453125, 'method_loss': 904.2598876953125}


### Load Goal Pricerange Predictor Model

In [46]:
model_GoalPricerangePredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                                   output_dim = PREDICTOR_DIM,
                                                   device = DEVICE).to(DEVICE)
model_GoalPricerangePredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalPricerangePredictor.pt"))
model_GoalPricerangePredictor.eval()

iDSTPredictorModel(
  (classifier): Linear(in_features=100, out_features=2, bias=True)
)

### Load Goal Area Predictor Model

In [47]:
model_GoalAreaPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                             output_dim = PREDICTOR_DIM,
                                             device = DEVICE).to(DEVICE)
model_GoalAreaPredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalAreaPredictor.pt"))
model_GoalAreaPredictor.eval()

iDSTPredictorModel(
  (classifier): Linear(in_features=100, out_features=2, bias=True)
)

### Load Goal Name Predictor Model

In [48]:
model_GoalNamePredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                             output_dim = PREDICTOR_DIM,
                                             device = DEVICE).to(DEVICE)
model_GoalNamePredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalNamePredictor.pt"))
model_GoalNamePredictor.eval()

iDSTPredictorModel(
  (classifier): Linear(in_features=100, out_features=2, bias=True)
)

### Load Goal Food Predictor Model

In [49]:
model_GoalFoodPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                             output_dim = PREDICTOR_DIM,
                                             device = DEVICE).to(DEVICE)
model_GoalFoodPredictor.load_state_dict(torch.load("model_PANFMR_incremental_GoalFoodPredictor.pt"))
model_GoalFoodPredictor.eval()

iDSTPredictorModel(
  (classifier): Linear(in_features=100, out_features=2, bias=True)
)

### Load Requested Predictor Model

In [50]:
model_RequestedPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                              output_dim = PREDICTOR_DIM,
                                              device = DEVICE).to(DEVICE)
model_RequestedPredictor.load_state_dict(torch.load("model_PANFMR_incremental_RequestedPredictor.pt"))
model_RequestedPredictor.eval()

iDSTPredictorModel(
  (classifier): Linear(in_features=100, out_features=2, bias=True)
)

### Load Method Predictor Model

In [51]:
model_MethodPredictor = iDSTPredictorModel(hidden_dim = HIDDEN_DIM,
                                           output_dim = PREDICTOR_DIM,
                                           device = DEVICE).to(DEVICE)
model_MethodPredictor.load_state_dict(torch.load("model_PANFMR_incremental_MethodPredictor.pt"))
model_MethodPredictor.eval()

iDSTPredictorModel(
  (classifier): Linear(in_features=100, out_features=2, bias=True)
)

### Print losses

In [52]:
dev_losses_dict = get_predictor_loss(model_GoalPricerange, model_GoalArea, model_GoalName,
                                     model_GoalFood, model_Requested, model_Method,
                                     model_GoalPricerangePredictor, model_GoalAreaPredictor, model_GoalNamePredictor,
                                     model_GoalFoodPredictor, model_RequestedPredictor, model_MethodPredictor,
                                     raw_X_dev, dev_predictor_Y, DEVICE)
pprint(dev_losses_dict)

{'goal_area_loss': 545.0855712890625,
 'goal_food_loss': 820.1277465820312,
 'goal_name_loss': 0.06962546706199646,
 'goal_pricerange_loss': 421.03070068359375,
 'method_loss': 904.2598876953125,
 'requested_all_loss': 1111.31689453125}


### Plotting

In [53]:
dev_predictor_tracker, \
dev_predictor_percentage_point, \
dev_predictor_percentage_points, \
dev_predictor_token_points = make_predictor_tracker(model_GoalPricerange, model_GoalArea, model_GoalName,
                                                    model_GoalFood, model_Requested, model_Method,
                                                    model_GoalPricerangePredictor, model_GoalAreaPredictor, model_GoalNamePredictor,
                                                    model_GoalFoodPredictor, model_RequestedPredictor, model_MethodPredictor,
                                                    raw_X_dev, raw_Y_dev, dataset = "dstc2_dev", threshold = 0.70)
print("DEV Predictor percentage point: {}".format(dev_predictor_percentage_point))
dev_predictor_tracker_scores_dict = get_scores(dev_predictor_tracker, dataset = "dstc2_dev", ontology = ontology)
pprint(dev_predictor_tracker_scores_dict)

[('welcomemsg', 0.0), ('i', -0.203985), ('would', -0.203985), ('like', -0.203985), ('to', -0.203985), ('find', -0.203985), ('an', -0.203985), ('expensive', -0.203985), ('restaurant', -0.203985), ('in', -0.203985), ('the', -0.203985), ('south', -0.203985)]
('welcomemsg', 0.0)
PRICERANGE = 0.44468486309051514
NAME = 0.9999880194664001
AREA = 0.825417160987854
FOOD = 0.8383560180664062
REQUESTED = 0.9960628747940063
METHOD = 0.950218141078949


('i', -0.203985)
PRICERANGE = 0.43526366353034973
NAME = 0.9999880194664001
AREA = 0.5883108973503113
FOOD = 0.7082775235176086
REQUESTED = 0.9989012479782104
METHOD = 0.9938027262687683


('would', -0.203985)
PRICERANGE = 0.44875016808509827
NAME = 0.9999871253967285
AREA = 0.8207037448883057
FOOD = 0.6723610162734985
REQUESTED = 0.9986050724983215
METHOD = 0.9960626363754272


('like', -0.203985)
PRICERANGE = 0.4448714256286621
NAME = 0.9999880194664001
AREA = 0.7976831793785095
FOOD = 0.8105341792106628
REQUESTED = 0.9985783100128174
METHOD = 0.

REQUESTED = 0.9024196863174438
METHOD = 0.6919432878494263


('taj tandoori', 0.0)
PRICERANGE = 0.45564448833465576
NAME = 0.9999871253967285
AREA = 0.998323917388916
FOOD = 0.9995063543319702
REQUESTED = 0.9829060435295105
METHOD = 0.689531147480011


('inform', 0.0)
PRICERANGE = 0.4435116648674011
NAME = 0.9999880194664001
AREA = 0.9989631772041321
FOOD = 0.9995540380477905
REQUESTED = 0.9629660248756409
METHOD = 0.7653929591178894


('food', 0.0)
PRICERANGE = 0.437856525182724
NAME = 0.9999875426292419
AREA = 0.9987912178039551
FOOD = 0.9993553161621094
REQUESTED = 0.9676949381828308
METHOD = 0.6626061201095581


('indian', 0.0)
PRICERANGE = 0.42899730801582336
NAME = 0.9999866485595703
AREA = 0.9985776543617249
FOOD = 0.9992488026618958
REQUESTED = 0.9746978282928467
METHOD = 0.7101464867591858


('okay', -1.268168)
PRICERANGE = 0.4368527829647064
NAME = 0.9999871253967285
AREA = 0.998307466506958
FOOD = 0.9995118379592896
REQUESTED = 0.9884999990463257
METHOD = 0.7337175011634827


[('offer', 0.0), ('name', 0.0), ('royal spice', 0.0), ('inform', 0.0), ('addr', 0.0), ('victoria avenue chesterton', 0.0), ('and', -0.115424), ('the', -0.115424), ('phone', -0.115424), ('number', -0.115424)]
('offer', 0.0)
PRICERANGE = 0.4405333399772644
NAME = 0.9999880194664001
AREA = 0.9745930433273315
FOOD = 0.9911414384841919
REQUESTED = 0.44705840945243835
METHOD = 0.885364830493927


('name', 0.0)
PRICERANGE = 0.4401543140411377
NAME = 0.9999880194664001
AREA = 0.9750771522521973
FOOD = 0.9907549023628235
REQUESTED = 0.5469651818275452
METHOD = 0.8636230826377869


('royal spice', 0.0)
PRICERANGE = 0.4466422498226166
NAME = 0.9999871253967285
AREA = 0.9796462059020996
FOOD = 0.9923281669616699
REQUESTED = 0.6451683044433594
METHOD = 0.8757217526435852


('inform', 0.0)
PRICERANGE = 0.4434607923030853
NAME = 0.9999880194664001
AREA = 0.9948024749755859
FOOD = 0.989949107170105
REQUESTED = 0.5113783478736877
METHOD = 0.7994118928909302


('addr', 0.0)
PRICERANGE = 0.44090300798416

('offer', 0.0)
PRICERANGE = 0.44096627831459045
NAME = 0.9999880194664001
AREA = 0.9947890639305115
FOOD = 0.997729480266571
REQUESTED = 0.6026843786239624
METHOD = 0.7548926472663879


('name', 0.0)
PRICERANGE = 0.4402559995651245
NAME = 0.9999880194664001
AREA = 0.9946326613426208
FOOD = 0.9973176121711731
REQUESTED = 0.6913877725601196
METHOD = 0.7093936204910278


('pipasha restaurant', 0.0)
PRICERANGE = 0.4336176812648773
NAME = 0.9999871253967285
AREA = 0.9944847822189331
FOOD = 0.9968972206115723
REQUESTED = 0.8110948204994202
METHOD = 0.649596095085144


('inform', 0.0)
PRICERANGE = 0.44335296750068665
NAME = 0.9999880194664001
AREA = 0.9960688352584839
FOOD = 0.9980787634849548
REQUESTED = 0.7465869784355164
METHOD = 0.6985102295875549


('pricerange', 0.0)
PRICERANGE = 0.436781108379364
NAME = 0.9999875426292419
AREA = 0.9956813454627991
FOOD = 0.9982707500457764
REQUESTED = 0.6688559651374817
METHOD = 0.577109694480896


('expensive', 0.0)
PRICERANGE = 0.4420439302921295
NAM

[('offer', 0.0), ('name', 0.0), ('the nirala', 0.0), ('inform', 0.0), ('food', 0.0), ('indian', 0.0), ('inform', 0.0), ('pricerange', 0.0), ('moderate', 0.0), ('address', -0.01272)]
('offer', 0.0)
PRICERANGE = 0.4408439099788666
NAME = 0.9999880194664001
AREA = 0.9998169541358948
FOOD = 0.9989520311355591
REQUESTED = 0.7287188172340393
METHOD = 0.6669403314590454


('name', 0.0)
PRICERANGE = 0.4402259886264801
NAME = 0.9999880194664001
AREA = 0.999842643737793
FOOD = 0.9988398551940918
REQUESTED = 0.8271923065185547
METHOD = 0.6469557881355286


('the nirala', 0.0)
PRICERANGE = 0.447569340467453
NAME = 0.9999871253967285
AREA = 0.999842643737793
FOOD = 0.9994450807571411
REQUESTED = 0.8020859956741333
METHOD = 0.6309128403663635


('inform', 0.0)
PRICERANGE = 0.4436185657978058
NAME = 0.9999880194664001
AREA = 0.9998959898948669
FOOD = 0.9991587400436401
REQUESTED = 0.883101224899292
METHOD = 0.7151858806610107


('food', 0.0)
PRICERANGE = 0.43784207105636597
NAME = 0.9999875426292419


...

NAME = 0.9999880194664001
AREA = 0.993070125579834
FOOD = 0.9994138479232788
REQUESTED = 0.9332189559936523
METHOD = 0.9613730907440186


('food', -0.196798)
PRICERANGE = 0.4378599524497986
NAME = 0.9999880194664001
AREA = 0.9900193214416504
FOOD = 0.9985368847846985
REQUESTED = 0.933081328868866
METHOD = 0.9557969570159912


('do', -0.196798)
PRICERANGE = 0.44215312600135803
NAME = 0.9999880194664001
AREA = 0.9925238490104675
FOOD = 0.999284565448761
REQUESTED = 0.8398017287254333
METHOD = 0.9307880401611328


[('offer', 0.0), ('name', 0.0), ('the nirala', 0.0), ('inform', 0.0), ('food', 0.0), ('indian', 0.0), ('thank', -0.734669), ('you', -0.734669), ('goodbye', -0.734669)]
('offer', 0.0)
PRICERANGE = 0.44062066078186035
NAME = 0.9999880194664001
AREA = 0.9890143871307373
FOOD = 0.9991356134414673
REQUESTED = 0.6812670230865479
METHOD = 0.5644024610519409


('name', 0.0)
PRICERANGE = 0.4401704967021942
NAME = 0.9999880194664001
AREA = 0.9919205904006958
FOOD = 0.9989426732063293
REQU

[('offer', 0.0), ('name', 0.0), ('taj tandoori', 0.0), ('inform', 0.0), ('pricerange', 0.0), ('expensive', 0.0), ('thank', -0.503732), ('you', -0.503732), ('goodbye', -0.503732)]
('offer', 0.0)
PRICERANGE = 0.4408363401889801
NAME = 0.9999880194664001
AREA = 0.9982710480690002
FOOD = 0.9948853850364685
REQUESTED = 0.7177548408508301
METHOD = 0.7485512495040894


('name', 0.0)
PRICERANGE = 0.4402211606502533
NAME = 0.9999880194664001
AREA = 0.9982894062995911
FOOD = 0.9950777888298035
REQUESTED = 0.833947479724884
METHOD = 0.729139506816864


('taj tandoori', 0.0)
PRICERANGE = 0.4557068943977356
NAME = 0.9999871253967285
AREA = 0.9983953237533569
FOOD = 0.996293306350708
REQUESTED = 0.9635434746742249
METHOD = 0.6596139073371887


('inform', 0.0)
PRICERANGE = 0.4435366094112396
NAME = 0.9999880194664001
AREA = 0.9990139007568359
FOOD = 0.9961200952529907
REQUESTED = 0.9351824522018433
METHOD = 0.7269701361656189


('pricerange', 0.0)
PRICERANGE = 0.43680644035339355
NAME = 0.99998754262

AREA = 0.998214840888977
FOOD = 0.9390307068824768
REQUESTED = 0.5471996665000916
METHOD = 0.9288347959518433


('inform', 0.0)
PRICERANGE = 0.443494975566864
NAME = 0.9999871253967285
AREA = 0.9980685114860535
FOOD = 0.9699772000312805
REQUESTED = 0.41282808780670166
METHOD = 0.9569087624549866


('pricerange', 0.0)
PRICERANGE = 0.43679147958755493
NAME = 0.9999880194664001
AREA = 0.9964199066162109
FOOD = 0.9795244336128235
REQUESTED = 0.33268317580223083
METHOD = 0.9497847557067871


('expensive', 0.0)
PRICERANGE = 0.44204574823379517
NAME = 0.9999880194664001
AREA = 0.9972341060638428
FOOD = 0.978347659111023
REQUESTED = 0.447780579328537
METHOD = 0.924386203289032


('phone', -0.000871)
PRICERANGE = 0.4426761865615845
NAME = 0.9999880194664001
AREA = 0.9987278580665588
FOOD = 0.9833858609199524
REQUESTED = 0.8981979489326477
METHOD = 0.9744274616241455


[('offer', 0.0), ('name', 0.0), ('michaelhouse cafe', 0.0), ('phone', -0.058684), ('number', -0.058684)]
('offer', 0.0)
PRICERAN

AREA = 0.9744009971618652
FOOD = 0.7612622976303101
REQUESTED = 0.9984971284866333
METHOD = 0.9680787920951843


('stop', -4.546748)
PRICERANGE = 0.45018452405929565
NAME = 0.9999880194664001
AREA = 0.9722451567649841
FOOD = 0.7782874703407288
REQUESTED = 0.9995113015174866
METHOD = 0.9882863759994507


('particular', -4.546748)
PRICERANGE = 0.4403167963027954
NAME = 0.9999880194664001
AREA = 0.995265007019043
FOOD = 0.8480513691902161
REQUESTED = 0.9990906119346619
METHOD = 0.9900805950164795


[('canthelp', 0.0), ('food', 0.0), ('polynesian', 0.0), ('how', -0.716118), ('about', -0.716118), ('italian', -0.716118), ('food', -0.716118)]
('canthelp', 0.0)
PRICERANGE = 0.4315159022808075
NAME = 0.9999880194664001
AREA = 0.9938991665840149
FOOD = 0.7981457710266113
REQUESTED = 0.997113049030304
METHOD = 0.7001683712005615


('food', 0.0)
PRICERANGE = 0.43776965141296387
NAME = 0.9999880194664001
AREA = 0.996928870677948
FOOD = 0.641756534576416
REQUESTED = 0.9980559349060059
METHOD = 0.780

('inform', 0.0)
PRICERANGE = 0.44338521361351013
NAME = 0.9999871253967285
AREA = 0.9981073141098022
FOOD = 0.9929240345954895
REQUESTED = 0.6626299023628235
METHOD = 0.7918026447296143


('area', 0.0)
PRICERANGE = 0.4366846978664398
NAME = 0.9999880194664001
AREA = 0.990217387676239
FOOD = 0.9906094074249268
REQUESTED = 0.6768540740013123
METHOD = 0.8517731428146362


('north', 0.0)
PRICERANGE = 0.44411879777908325
NAME = 0.9999880194664001
AREA = 0.9725245237350464
FOOD = 0.9906561374664307
REQUESTED = 0.6685011386871338
METHOD = 0.8273399472236633


('what', -1.780605)
PRICERANGE = 0.4429137408733368
NAME = 0.9999880194664001
AREA = 0.9894094467163086
FOOD = 0.9910702705383301
REQUESTED = 0.5832020044326782
METHOD = 0.9821292757987976


[('offer', 0.0), ('name', 0.0), ('da vinci pizzeria', 0.0), ('inform', 0.0), ('food', 0.0), ('italian', 0.0), ('thank', -0.540482), ('you', -0.540482), ('goodbye', -0.540482)]
('offer', 0.0)
PRICERANGE = 0.4406368136405945
NAME = 0.9999880194664001
A

In [ ]:
plotly_plot_histogram2d(dev_predictor_percentage_points, dev_predictor_token_points, "dstc2_dev")

In [ ]:
test_predictor_tracker, \
test_predictor_percentage_point, \
test_predictor_percentage_points, \
test_predictor_token_points = make_predictor_tracker(model_GoalPricerange, model_GoalArea, model_GoalName,
                                                     model_GoalFood, model_Requested, model_Method,
                                                     model_GoalPricerangePredictor, model_GoalAreaPredictor, model_GoalNamePredictor,
                                                     model_GoalFoodPredictor, model_RequestedPredictor, model_MethodPredictor,
                                                     raw_X_test, raw_Y_test, "dstc2_test", threshold = 0.30)
print("TEST Predictor percentage point: {}".format(test_predictor_percentage_point))
test_predictor_tracker_scores_dict = get_scores(test_predictor_tracker, dataset = "dstc2_test", ontology = ontology)
pprint(test_predictor_tracker_scores_dict)

In [ ]:
plotly_plot_histogram2d(test_predictor_percentage_points, test_predictor_token_points, "dstc2_test")

In [ ]:
dev_goal_pricerange_accuracies = []
dev_goal_area_accuracies = []
dev_goal_name_accuracies = []
dev_goal_food_accuracies = []
dev_requested_accuracies = []
dev_method_accuracies = []
dev_percentages = []

test_goal_pricerange_accuracies = []
test_goal_area_accuracies = []
test_goal_name_accuracies = []
test_goal_food_accuracies = []
test_requested_accuracies = []
test_method_accuracies = []
test_percentages = []

percentages = list(frange(0.1, 1.05, 0.05))
for percentage in tqdm_notebook(percentages, total = len(percentages)):
    
    dev_incremental_tracker, dev_incremental_percentage = make_tracker(model_GoalPricerange, model_GoalArea, model_GoalName,
                                                                       model_GoalFood, model_Requested, model_Method,
                                                                       raw_X_dev, raw_Y_dev, dataset = "dstc2_dev", percentage = percentage)
    dev_percentages.append(dev_incremental_percentage)
    dev_scores_dict = get_scores(dev_incremental_tracker, dataset = "dstc2_dev", ontology = ontology)
    dev_goal_pricerange_accuracies.append(dev_scores_dict["goal_pricerange_accuracy"])
    dev_goal_area_accuracies.append(dev_scores_dict["goal_area_accuracy"])
    dev_goal_name_accuracies.append(dev_scores_dict["goal_name_accuracy"])
    dev_goal_food_accuracies.append(dev_scores_dict["goal_food_accuracy"])
    dev_requested_accuracies.append(dev_scores_dict["requested_all_accuracy"])
    dev_method_accuracies.append(dev_scores_dict["method_accuracy"])
    
    test_incremental_tracker, test_incremental_percentage = make_tracker(model_GoalPricerange, model_GoalArea, model_GoalName,
                                                                         model_GoalFood, model_Requested, model_Method,
                                                                         raw_X_test, raw_Y_test, dataset = "dstc2_test", percentage = percentage)
    test_percentages.append(test_incremental_percentage)
    test_scores_dict = get_scores(test_incremental_tracker, dataset = "dstc2_test", ontology = ontology)
    test_goal_pricerange_accuracies.append(test_scores_dict["goal_pricerange_accuracy"])
    test_goal_area_accuracies.append(test_scores_dict["goal_area_accuracy"])
    test_goal_name_accuracies.append(test_scores_dict["goal_name_accuracy"])
    test_goal_food_accuracies.append(test_scores_dict["goal_food_accuracy"])
    test_requested_accuracies.append(test_scores_dict["requested_all_accuracy"])
    test_method_accuracies.append(test_scores_dict["method_accuracy"])

In [ ]:
plotly_plot_incremental(dev_goal_pricerange_accuracies, dev_goal_area_accuracies, dev_goal_name_accuracies, dev_goal_food_accuracies,
                        dev_requested_accuracies, dev_method_accuracies, dev_percentages, dev_predictor_percentage_point,
                        dev_predictor_tracker_scores_dict["goal_pricerange_accuracy"], dev_predictor_tracker_scores_dict["goal_area_accuracy"], dev_predictor_tracker_scores_dict["goal_name_accuracy"],
                        dev_predictor_tracker_scores_dict["goal_food_accuracy"], dev_predictor_tracker_scores_dict["requested_all_accuracy"], dev_predictor_tracker_scores_dict["method_accuracy"], "dstc2_dev")

In [ ]:
plotly_plot_incremental(test_goal_pricerange_accuracies, test_goal_area_accuracies, test_goal_name_accuracies, test_goal_food_accuracies,
                        test_requested_accuracies, test_method_accuracies, test_percentages, test_predictor_percentage_point,
                        test_predictor_tracker_scores_dict["goal_pricerange_accuracy"], test_predictor_tracker_scores_dict["goal_area_accuracy"], test_predictor_tracker_scores_dict["goal_name_accuracy"],
                        test_predictor_tracker_scores_dict["goal_food_accuracy"], test_predictor_tracker_scores_dict["requested_all_accuracy"], test_predictor_tracker_scores_dict["method_accuracy"], "dstc2_test")